In [1]:
# IMPORT STATEMENTS
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import math
import pandas as pd
import scanpy as sc
import os
import GEOparse

In [42]:
# These functions are in moreprocessing.py

def getDataInfo():
    '''Get the accession ID, GPL (platform name) and filepath for the Hegemon files.'''
    path_dir = os.getcwd()
    accessionID = path_dir.split("/")[-1]
    gse = GEOparse.get_GEO(geo=str(accessionID), destdir=path_dir)
    gpl = list(gse.gpls.keys())[0]
    filepath = path_dir+"/"+str(accessionID)+'-%s'%(gpl)
    return accessionID, gpl, filepath

def make_idx(expr_name, idx_name):
    '''Build index file from expression file.'''
    print('Starting make_idx')
    expr = expr_name

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(idx_name, 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")

def writeExprIdx(expr):
    '''Write both index and expression file from the expression file as a dataframe.'''
    accessionID, gpl, filepath = getDataInfo()
    expr_name = "%s-expr.txt" % filepath
    idx_name = "%s-idx.txt" % filepath
    print("Starting expr")
    expr.to_csv(expr_name, header=True, index=False,sep='\t')
    print("Done writing expr")
    make_idx(expr_name, idx_name)
    
def printConf(dbid, name, key =''):
    '''Print the information needed to add the dataset to explore.conf (configuration file).'''
    accessionID, gpl, filepath = getDataInfo()
    print("[%s]" % dbid)
    print("name = %s" % name)
    print("expr = %s-expr.txt" % filepath)
    print("index = %s-idx.txt" % filepath)
    print("survival = %s-survival.txt" % filepath)
    print("indexHeader = %s-ih.txt" % filepath)
    print("info = %s-info.txt" % filepath)
    print("key = %s" % key)
    print("source = %s" % accessionID)
    
def writeConf(dbid, name, key='', cf="/Users/rohan/public_html/Hegemon/explore.conf"):
    '''Write the information to add the dataset to explore.conf (configuration file).'''
    accessionID, gpl, filepath = getDataInfo()
    with open(cf, 'a') as f:
        f.write("\n[%s]\n" % dbid)
        f.write("name = %s\n" % name)
        f.write("expr = %s-expr.txt\n" % filepath)
        f.write("index = %s-idx.txt\n" % filepath)
        f.write("survival = %s-survival.txt\n" % filepath)
        f.write("indexHeader = %s-ih.txt\n" % filepath)
        f.write("info = %s-info.txt\n" % filepath)
        f.write("key = %s\n" % key)
        f.write("source = %s\n" % accessionID)

In [41]:
# Read raw counts
expr = pd.DataFrame(pd.read_csv('GSE154311_htseq_rawCounts.txt', sep = '\t', header=0))
# Use information in ih file to replace expr headers with GSMIDs
ih_df = pd.DataFrame(pd.read_csv('GSE154311-GPL18573-ih.txt', sep = '\t', header=0))
expr.columns = ["ProbeID"]+list(ih_df["ArrayID"])
# Use gene annotation tables to get gene name from each ensembl ID
ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Homo_sapiens.GRCh38.99.chr_patch_hapl_scaff.txt", sep = '\t', header=None)) 
ensembl_df.columns = ["ProbeID", "Name"]
expr = ensembl_df.merge(expr, how="right",on="ProbeID")
expr

ProbeID        Name  GSM4668813  GSM4668814  GSM4668815  \
0      ENSG00000000003      TSPAN6           0           0           0   
1      ENSG00000000005        TNMD           0           0           0   
2      ENSG00000000419        DPM1         229         363         569   
3      ENSG00000000457       SCYL3         156         217         349   
4      ENSG00000000460    C1orf112          23          44          43   
...                ...         ...         ...         ...         ...   
44447  ENSG00000285498  AC104389.7           0           0           0   
44448  ENSG00000285505  AC010616.1           0           0           0   
44449  ENSG00000285508  AL034430.1           0           0           0   
44450  ENSG00000285509  AP000646.1           0           0           0   
44451  ENSG00000285513  AP006216.3           0           0           0   

       GSM4668816  GSM4668817  GSM4668818  GSM4668819  GSM4668820  GSM4668821  
0               0           2           1           0           0           0  
1               0           0           0           0           0           0  
2             193         221         192         256         285         248  
3             313         185         263         254         180         251  
4               7          22          38         118         153         101  
...           ...         ...         ...         ...         ...         ...  
44447           0           0           0           0           0           0  
44448           0           0           0           0           0           0  
44449           0           0           0           0           0           0  
44450           0           0           0           1           0           0  
44451           0           0           0           0           0           0  

[44452 rows x 11 columns]

In [22]:
genes = expr.loc[:,["ProbeID", "Name"]]
cols = expr.columns

# Normalize using TPM and log transform
expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID        Name  GSM4668813  GSM4668814  GSM4668815  \
0      ENSG00000000003      TSPAN6    0.000000    0.000000    0.000000   
1      ENSG00000000005        TNMD    0.000000    0.000000    0.000000   
2      ENSG00000000419        DPM1    4.454158    4.747519    4.566058   
3      ENSG00000000457       SCYL3    3.930831    4.040933    3.898748   
4      ENSG00000000460    C1orf112    1.632784    2.047832    1.440701   
...                ...         ...         ...         ...         ...   
44447  ENSG00000285498  AC104389.7    0.000000    0.000000    0.000000   
44448  ENSG00000285505  AC010616.1    0.000000    0.000000    0.000000   
44449  ENSG00000285508  AL034430.1    0.000000    0.000000    0.000000   
44450  ENSG00000285509  AP000646.1    0.000000    0.000000    0.000000   
44451  ENSG00000285513  AP006216.3    0.000000    0.000000    0.000000   

       GSM4668816  GSM4668817  GSM4668818  GSM4668819  GSM4668820  GSM4668821  
0        0.000000    0.182408    0.102119    0.000000    0.000000    0.000000  
1        0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
2        3.769109    3.990303    3.914850    4.381764    4.327211    4.434361  
3        4.425520    3.751338    4.342751    4.370994    3.705573    4.450910  
4        0.544207    1.311818    1.921153    3.343152    3.490492    3.232363  
...           ...         ...         ...         ...         ...         ...  
44447    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
44448    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
44449    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
44450    0.000000    0.000000    0.000000    0.107724    0.000000    0.000000  
44451    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  

[44452 rows x 11 columns]

In [ ]:
import pandas as pd
import scanpy as sc

# Run process.py but change the last few lines to this
'''
for _, gpl in gse.gpls.items():
    
    #if experimentType == 'm':
     #   m_analyze(gpl)
    #else:
     #   rna_analyze(gpl)
    survival_ih(gpl)
    #make_idx(gpl)
'''
%run /Users/rohan/public_html/Hegemon/Data2/Data/moreprocessing.py

# Read raw counts (may have to differ based on file format)
expr = pd.DataFrame(pd.read_csv('path-to-expression-matrix.txt', sep = '\t', header=0))

# Use information in ih file to replace expr headers with GSMIDs 
# May not be necessary, or you might have to find another way to find the GSMIDs
ih_df = pd.DataFrame(pd.read_csv('name-of-ih-file.txt', sep = '\t', header=0))
expr.columns = ["ProbeID"]+list(ih_df["ArrayID"])

# Use gene annotation tables to get gene name from each ensembl ID. May not be necessary. 
# For human
ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Homo_sapiens.GRCh38.99.chr_patch_hapl_scaff.txt", sep = '\t', header=None)) 
# For mouse
# ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Mus_musculus.GRCm38.94.txt", sep = '\t', header=None))
ensembl_df.columns = ["ProbeID", "Name"]
expr = ensembl_df.merge(expr, how="right",on="ProbeID")

# Write expr file to txt
path_dir = "./"
expr.to_csv(path_dir+"name-of-expr.txt", header=True, index=False,sep='\t')
# Then, use the make_idx function from process.py to make the idx file

# Alternatively, you can use this if the directory name is the GSEID (GSE154311)
# writeExprIdx(expr)

# You can use this to print the details you need to add to explore.conf if the directory name is the GSEID (GSE154311)
# printConf("NEU4", "Morissey 2020 Neutrophils COVID", key="neu:")
# printConf("Database ID", "Name of Dataset", key="key:")

# You can write the information directly to explore.conf (verify first though)
# writeConf("NEU4", "Morissey 2020 Neutrophils COVID", key="neu:", cf='path-to-your-explore.conf')

In [34]:
writeExprIdx(expr)

21-Jun-2022 14:55:44 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311 already exists. Skipping.
21-Jun-2022 14:55:44 INFO GEOparse - File already exist: using local version.
21-Jun-2022 14:55:44 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311_family.soft.gz: 
21-Jun-2022 14:55:44 DEBUG GEOparse - DATABASE: GeoMiame
21-Jun-2022 14:55:44 DEBUG GEOparse - SERIES: GSE154311
21-Jun-2022 14:55:44 DEBUG GEOparse - PLATFORM: GPL18573
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668813
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668814
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668815
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668816
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668817
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668818
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668819
21-Jun-2022 14:55:44 DEBUG GEOparse - SAMPLE: GSM4668820
21-Jun-2022 14:55:44 DEBU

Starting expr
Done writing expr to /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-expr.txt
Starting make_idx
Done with make_idx


In [36]:
printConf("NEU4", "Morissey 2020 Neutrophils COVID", key="neu:")
writeConf("NEU4", "Morissey 2020 Neutrophils COVID", key="neu:", cf='path-to-your-explore.conf')

21-Jun-2022 14:56:18 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311 already exists. Skipping.
21-Jun-2022 14:56:18 INFO GEOparse - File already exist: using local version.
21-Jun-2022 14:56:18 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311_family.soft.gz: 
21-Jun-2022 14:56:18 DEBUG GEOparse - DATABASE: GeoMiame
21-Jun-2022 14:56:18 DEBUG GEOparse - SERIES: GSE154311
21-Jun-2022 14:56:18 DEBUG GEOparse - PLATFORM: GPL18573
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668813
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668814
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668815
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668816
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668817
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668818
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668819
21-Jun-2022 14:56:18 DEBUG GEOparse - SAMPLE: GSM4668820
21-Jun-2022 14:56:18 DEBU

[NEU4]
name = Morissey 2020 Neutrophils COVID
expr = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-expr.txt
index = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-idx.txt
survival = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-survival.txt
indexHeader = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-ih.txt
info = /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE154311/GSE154311-GPL18573-info.txt
key = neu:
source = GSE154311
